In [1]:
import requests
import json

import openstreetmap_mapping as osm

import pandas as pd

from bokeh.plotting import show, output_file
from bokeh.io import output_notebook

from bokeh.plotting import figure
from bokeh.models import WMTSTileSource, ColumnDataSource
from bokeh.models import HoverTool

from pyproj import Transformer

output_notebook()

Loading BokehJS ...

In [2]:
%load_ext autoreload
%autoreload 2

In [3]:
class Tags(object):
    
    def __init__(self, *initial_data, **kwargs):
              
        for dictionary in initial_data:
            
            for key in dictionary:

                if isinstance(dictionary[key], dict):
                    if len(dictionary[key])>1:
                        setattr(self, 'value', key)
                        setattr(self, key, Tags(dictionary[key]))
                    else:
                        setattr(self, key, Tags(dictionary[key]))
                else:
                    setattr(self, key, dictionary[key])
            
    def __repr__(self):
        return self.value.replace("__",":")
    
    def __str__(self):
        return self.value.replace("__",":")

In [4]:
kvs = osm.toolkit.get_osm_kvs()

In [5]:
tags = Tags(kvs)

In [6]:
area_Glasgow = "(55.82, -4.34, 55.9, -4.22)"
area_London = "(51.3426, -0.5527, 51.6726, 0.1929)"
area_Moscow = "(55.503, 37.0789,56.003, 38.1871)"
area_Budapest = "(47.4439, 18.9315, 47.5851, 19.1711)"
area_Paris = "(48.744, 2.1265, 49.0316, 2.6099)"

In [7]:
df_stations = osm.toolkit.get_osm_data(key=tags.railway,tag=tags.railway.station,area=area_Glasgow)

In [8]:
df_stations["grouping"] = df_stations["network"]

In [9]:
df_stations['grouping'] = df_stations['grouping'].str.split(";",expand=True)[0]

In [10]:
df_stations = df_stations.dropna(subset=['grouping'])

In [11]:
output_file("Glasgow_Stations.html")

tooltips = {"tooltips":[("id", "@id"),("key", "@key"),("tag", "@tag"),("name", "@name"),("network", "@network"),("operator", "@operator"),("(lat,lon)", "@coordinates")]}

p = osm.toolkit.plot_latlon(df_stations,kwargs_for_figure=tooltips,kwargs_for_marker={"legend_group":"grouping"})

p.legend.visible = False

show(p)

In [12]:
df_station_subway = osm.toolkit.get_osm_data(key=tags.station,tag=tags.station.subway,area=area_Glasgow)


In [13]:
df_railway_subway = osm.toolkit.get_osm_data(key=tags.railway,tag=tags.railway.subway,area=area_Glasgow,output='geom')


In [14]:
from bokeh.plotting import figure
from bokeh.models import WMTSTileSource, ColumnDataSource
from bokeh.models import HoverTool

from pyproj import Transformer

# Use pyproj to transform longitude and latitude into web-mercator and add to a copy of the asset dataframe
TRANSFORM_4326_TO_3857 = Transformer.from_crs("EPSG:4326", "EPSG:3857")
    
# create a plot of the subway system    
output_file("Glasgow_subway.html")

p = figure(plot_width=800, plot_height=800,
                    x_axis_type="mercator", y_axis_type="mercator")

MAP_TILES = {"OpenMap": WMTSTileSource(url="http://c.tile.openstreetmap.org/{Z}/{X}/{Y}.png"),
         "ESRI": WMTSTileSource(url="https://server.arcgisonline.com/ArcGIS/rest/services/World_Imagery/MapServer/tile/{Z}/{Y}/{X}.jpg"),
         "OpenTopoMap": WMTSTileSource(url="https://tile.opentopomap.org/{Z}/{X}/{Y}.png")}
    
p.add_tile(MAP_TILES['ESRI'])

tooltips = [("id", "@id"),("key", "@key"),("tag", "@tag"),("name", "@name"),("network", "@network"),("operator", "@operator"),("(lat,lon)", "@coordinates")]


# plot the railway lines
for row in df_railway_subway.iterrows():
    way=pd.DataFrame.from_records(row[1]['geometry'])
       
    x,y = TRANSFORM_4326_TO_3857.transform(way['lat'],way['lon'])   
    
    p.line(x=x,y=y,line_width=2,line_color='orange',legend_label=row[1]['name'])
    
    
    
    
# plot the stations and add a hover tool
map_df = df_station_subway[['id','lat','lon','key','tags','tag','name','network','operator']].copy()

map_df["x"],map_df["y"] = TRANSFORM_4326_TO_3857.transform(map_df['lat'],map_df['lon'])  
map_df["coordinates"]=tuple(zip(map_df["lat"],map_df["lon"]))
map_df['tags'] = map_df['tags'].apply(str)
map_df['tag'] = map_df['tag'].apply(str)
map_df['key'] = map_df['key'].apply(str)


source = ColumnDataSource(map_df)


for legend_group in set(map_df["network"]):
    
    stations = p.scatter(x="x", y="y",
             source=source,
             size=14,
             line_width=3,
             fill_color = "white",
             line_color='orange',
             legend_label=legend_group)

    p.add_tools(HoverTool(tooltips=tooltips, renderers=[stations]))
    
    
show(p)

In [15]:
df_station_subway = osm.toolkit.get_osm_data(key=tags.station,tag=tags.station.subway,area=area_London)


In [16]:
df_railway_subway = osm.toolkit.get_osm_data(key=tags.railway,tag=tags.railway.subway,area=area_London,output='geom')


In [17]:
df_railway_subway['line'] = df_railway_subway['line'].fillna('Service')

df_railway_subway['first_line'] = df_railway_subway['line'].apply(lambda x: str(x).split(';')[0])

In [18]:
from bokeh.plotting import figure
from bokeh.models import WMTSTileSource, ColumnDataSource
from bokeh.models import HoverTool

from pyproj import Transformer

# Use pyproj to transform longitude and latitude into web-mercator and add to a copy of the asset dataframe
TRANSFORM_4326_TO_3857 = Transformer.from_crs("EPSG:4326", "EPSG:3857")
    
# create a plot of the subway system    
output_file("London_subway.html")

color_mapping = {'Central':'red',
                 'Piccadilly':'navy',
                 'Northern':'black',
                 'Victoria':'skyblue',
                 'Metropolitan':'purple',
                 'District':'green',
                 'Circle':'yellow',
                 'Bakerloo':'brown',
                 'Jubilee':'silver',
                 'Hammersmith & City':'pink',
                 'Northern City':'black',
                 'Overground':'orange',
                 'Waterloo & City':'teal',
                 'Service':'white',
                 'Other':'white',
                }

p = figure(plot_width=800, plot_height=800,
                    x_axis_type="mercator", y_axis_type="mercator")

MAP_TILES = {"OpenMap": WMTSTileSource(url="http://c.tile.openstreetmap.org/{Z}/{X}/{Y}.png"),
         "ESRI": WMTSTileSource(url="https://server.arcgisonline.com/ArcGIS/rest/services/World_Imagery/MapServer/tile/{Z}/{Y}/{X}.jpg"),
         "OpenTopoMap": WMTSTileSource(url="https://tile.opentopomap.org/{Z}/{X}/{Y}.png")}
    
p.add_tile(MAP_TILES['ESRI'])

tooltips = [("id", "@id"),
            ("key", "@key"),
            ("tag", "@tag"),
            ("name", "@name"),
            ("line", "@line"),
            ("network", "@network"),
            ("operator", "@operator"),
            ("(lat,lon)", "@coordinates")]


# plot the railway lines    
for line in set(df_railway_subway['line']):

    #print(line)
    
    df_lines = df_railway_subway.loc[df_railway_subway['line']==line]
  
    xx = list()
    yy = list()
    dashes = list()
    
    railway_lines = line.replace(',', ';').split(';')
    
    for row in df_lines['geometry']:
    
        xxx,yyy = TRANSFORM_4326_TO_3857.transform(list(pd.DataFrame.from_records(row)['lat']),
                                                 list(pd.DataFrame.from_records(row)['lon']))
    
        xx.append(xxx)
        yy.append(yyy)
        
        if len(xxx)%2 == 0:
            dashes.append([5,5*(len(railway_lines)-1)]*int(len(xxx)/2))
        else:
            dashes.append([5,5*(len(railway_lines)-1)]*int(len(xxx)/2-0.5)+[5])
            
    
    source = ColumnDataSource({'xs':xx,'ys':yy,'line_dash':dashes})
    
    if len(railway_lines) == 1:
        line_dash = 'solid'
    else:
        line_dash = 'line_dash'
             
    for cnt,railway_line in enumerate(railway_lines):

            railway_line = railway_line.strip()

            p.multi_line('xs',
                   'ys',
                   source=source,
                   line_width=2,
                   legend_label=str(railway_line),
                   line_color = color_mapping[railway_line],
                   line_dash = line_dash,
                   line_dash_offset = cnt*5
                  )

    
    
# plot the stations and add a hover tool
map_df = df_station_subway[['id','lat','lon','key','tags','tag','name','line','network','operator']].copy()

map_df["x"],map_df["y"] = TRANSFORM_4326_TO_3857.transform(map_df['lat'],map_df['lon'])  
map_df["coordinates"]=tuple(zip(map_df["lat"],map_df["lon"]))
map_df['tags'] = map_df['tags'].apply(str)
map_df['tag'] = map_df['tag'].apply(str)
map_df['key'] = map_df['key'].apply(str)
map_df['line'] = map_df['line'].fillna('Other')

stations = list()
for legend_group in set(map_df["line"]):
    
    source = ColumnDataSource(map_df.loc[map_df["line"]==legend_group])

    
    station_lines = legend_group.split(';')
        
    for cnt,station_line in enumerate(station_lines):
        
        if len(station_lines)>1:
            
            station = p.wedge(x="x", y="y",
                            source=source,
                            start_angle=(cnt-1)/len(station_lines)*2*3.142,
                            end_angle=cnt/len(station_lines)*2*3.1412,
                            radius=100,
                            line_width=1,
                            fill_color = color_mapping[station_line],
                            line_color = 'white',
                            legend_label=station_line
                            )
            
        else:
        
            station = p.circle(x="x", y="y",
                            source=source,
                            radius=100,
                            line_width=1,
                            fill_color = color_mapping[station_line],
                            line_color = 'white',
                            legend_label=station_line
                            )
            
        stations.append(station)
    

p.add_tools(HoverTool(tooltips=tooltips, renderers=stations))

p.legend.click_policy="hide"
    
    
show(p)

In [40]:
df_station_subway = osm.toolkit.get_osm_data(key=tags.station,tag=tags.station.subway,area=area_Moscow)


In [41]:
df_railway_subway = osm.toolkit.get_osm_data(key=tags.railway,tag=tags.railway.subway,area=area_Moscow,output='geom')


In [42]:
df_railway_subway['line'] = df_railway_subway['name'].fillna('Service')

df_railway_subway['first_line'] = df_railway_subway['line'].apply(lambda x: str(x).split(';')[0])

In [44]:


# Use pyproj to transform longitude and latitude into web-mercator and add to a copy of the asset dataframe
TRANSFORM_4326_TO_3857 = Transformer.from_crs("EPSG:4326", "EPSG:3857")
    
# create a plot of the subway system    
output_file("Moscow_subway.html")

color_mapping = {'Кольцевая линия':'brown',
            'Некрасовская линия':'pink',
            'Ответвление ТКЛ-КожЛ':'purple',
            'Калининская линия':'yellow',
            'Бутовская линия':'lightblue',
            'Служебная соединительная ветвь':'white',
            '3-6':'gray',
            'Каховская линия':'black',
            'Калужско-Рижская линия':'orange',
            'Большая кольцевая линия':'#82C0C0',
            'Люблинско-Дмитровская линия':'#b4d445',
            'Филёвская линия':'lightblue',
            'Сокольническая линия':'red',
            'Серпуховско-Тимирязевская линия':'gray',
            'Арбатско-Покровская линия':'blue',
            'Третий станционный путь':'violet',
            'Третий пересадочный контур':'darkturquoise',
            'БКЛ':'#82C0C0',
            'Замоскворецкая линия':'darkgreen',
            'Калининско-Солнцевская линия':'yellow',
            'Таганско-Краснопресненская линия':'violet',
            '4-5':'gray',
            'Солнцевская линия':'yellow',
            '21':'red',
            'Service':'white',
            'Other':'white',
                }

p = figure(plot_width=800, plot_height=800,
                    x_axis_type="mercator", y_axis_type="mercator")

MAP_TILES = {"OpenMap": WMTSTileSource(url="http://c.tile.openstreetmap.org/{Z}/{X}/{Y}.png"),
         "ESRI": WMTSTileSource(url="https://server.arcgisonline.com/ArcGIS/rest/services/World_Imagery/MapServer/tile/{Z}/{Y}/{X}.jpg"),
         "OpenTopoMap": WMTSTileSource(url="https://tile.opentopomap.org/{Z}/{X}/{Y}.png")}
    
p.add_tile(MAP_TILES['ESRI'])

tooltips = [("id", "@id"),
            ("key", "@key"),
            ("tag", "@tag"),
            ("name", "@name"),
            ("line", "@line"),
            ("network", "@network"),
            ("operator", "@operator"),
            ("(lat,lon)", "@coordinates")]


# plot the railway lines    
for line in set(df_railway_subway['line']):

    #print(line)
    
    df_lines = df_railway_subway.loc[df_railway_subway['line']==line]
  
    xx = list()
    yy = list()
    dashes = list()

    railway_lines = line.replace(',', ';').split(';')
    
    for row in df_lines['geometry']:
    
        xxx,yyy = TRANSFORM_4326_TO_3857.transform(list(pd.DataFrame.from_records(row)['lat']),
                                                 list(pd.DataFrame.from_records(row)['lon']))
    
        xx.append(xxx)
        yy.append(yyy)
        
        
        if len(xxx)%2 == 0:
            dashes.append([5,5*(len(railway_lines)-1)]*int(len(xxx)/2))
        else:
            dashes.append([5,5*(len(railway_lines)-1)]*int(len(xxx)/2-0.5)+[5])
            
    
    source = ColumnDataSource({'xs':xx,'ys':yy,'line_dash':dashes})
    
    if len(railway_lines) == 1:
        line_dash = 'solid'
    else:
        line_dash = 'line_dash'
             
    for cnt,railway_line in enumerate(railway_lines):

            railway_line = railway_line.strip()

            p.multi_line('xs',
                   'ys',
                   source=source,
                   line_width=2,
                   legend_label=str(railway_line),
                   line_color = color_mapping[railway_line],
                   line_dash = line_dash,
                   line_dash_offset = cnt*5
                  )

    
    
# plot the stations and add a hover tool
map_df = df_station_subway[['id','lat','lon','key','tags','tag','name','colour','network','operator']].copy()

map_df["x"],map_df["y"] = TRANSFORM_4326_TO_3857.transform(map_df['lat'],map_df['lon'])  
map_df["coordinates"]=tuple(zip(map_df["lat"],map_df["lon"]))
map_df['tags'] = map_df['tags'].apply(str)
map_df['tag'] = map_df['tag'].apply(str)
map_df['key'] = map_df['key'].apply(str)
map_df['line'] = map_df['colour'].fillna('Other')

stations = list()
for legend_group in set(map_df["line"]):
    
    source = ColumnDataSource(map_df.loc[map_df["line"]==legend_group])

    
    station_lines = legend_group.split(';')
        
    for cnt,station_line in enumerate(station_lines):
        
        if len(station_lines)>1:
            
            station = p.wedge(x="x", y="y",
                            source=source,
                            start_angle=(cnt-1)/len(station_lines)*2*3.142,
                            end_angle=cnt/len(station_lines)*2*3.1412,
                            radius=100,
                            line_width=1,
                            fill_color = station_line,
                            line_color = 'white',
                            #legend_label=station_line
                            )
            
        else:
        
            station = p.circle(x="x", y="y",
                            source=source,
                            radius=100,
                            line_width=1,
                            fill_color = station_line,
                            line_color = 'white',
                            #legend_label=station_line
                            )
            
        stations.append(station)
    

p.add_tools(HoverTool(tooltips=tooltips, renderers=stations))

p.legend.click_policy="hide"
    
p.legend.visible = False    

show(p)

ERROR:bokeh.core.validation.check:E-1001 (BAD_COLUMN_NAME): Glyph refers to nonexistent column name. This could either be due to a misspelling or typo, or due to an expected column being missing. : key "fill_color" value "Other" [renderer: GlyphRenderer(id='117414', ...)]


ERROR:bokeh.core.validation.check:E-1001 (BAD_COLUMN_NAME): Glyph refers to nonexistent column name. This could either be due to a misspelling or typo, or due to an expected column being missing. : key "fill_color" value "Other" [renderer: GlyphRenderer(id='117414', ...)]


In [24]:
df_station_subway = osm.toolkit.get_osm_data(key=tags.station,tag=tags.station.subway,area=area_Budapest)


In [25]:
df_railway_subway = osm.toolkit.get_osm_data(key=tags.railway,tag=tags.railway.subway,area=area_Budapest,output='geom')


In [26]:
df_railway_subway['line'] = df_railway_subway['name'].fillna('Service')

df_railway_subway['first_line'] = df_railway_subway['line'].apply(lambda x: str(x).split(';')[0])

In [27]:
from bokeh.plotting import figure
from bokeh.models import WMTSTileSource, ColumnDataSource
from bokeh.models import HoverTool

from pyproj import Transformer

# Use pyproj to transform longitude and latitude into web-mercator and add to a copy of the asset dataframe
TRANSFORM_4326_TO_3857 = Transformer.from_crs("EPSG:4326", "EPSG:3857")
    
# create a plot of the subway system    
output_file("Budapest_subway.html")

color_mapping = {'M1':'yellow',
                 'M2':'red',
                 'M3':'blue',
                 'M4':'green',
            'Service':'white',
            'Other':'white',
                }

p = figure(plot_width=800, plot_height=800,
                    x_axis_type="mercator", y_axis_type="mercator")

MAP_TILES = {"OpenMap": WMTSTileSource(url="http://c.tile.openstreetmap.org/{Z}/{X}/{Y}.png"),
         "ESRI": WMTSTileSource(url="https://server.arcgisonline.com/ArcGIS/rest/services/World_Imagery/MapServer/tile/{Z}/{Y}/{X}.jpg"),
         "OpenTopoMap": WMTSTileSource(url="https://tile.opentopomap.org/{Z}/{X}/{Y}.png")}
    
p.add_tile(MAP_TILES['ESRI'])

tooltips = [("id", "@id"),
            ("key", "@key"),
            ("tag", "@tag"),
            ("name", "@name"),
            ("line", "@line"),
            ("operator", "@operator"),
            ("(lat,lon)", "@coordinates")]


# plot the railway lines    
for line in set(df_railway_subway['line']):

    #print(line)
    
    df_lines = df_railway_subway.loc[df_railway_subway['line']==line]
  
    xx = list()
    yy = list()
    dashes = list()

    railway_lines = line.replace(',', ';').split(';')
    
    for row in df_lines['geometry']:
    
        xxx,yyy = TRANSFORM_4326_TO_3857.transform(list(pd.DataFrame.from_records(row)['lat']),
                                                 list(pd.DataFrame.from_records(row)['lon']))
    
        xx.append(xxx)
        yy.append(yyy)
        
        
        if len(xxx)%2 == 0:
            dashes.append([5,5*(len(railway_lines)-1)]*int(len(xxx)/2))
        else:
            dashes.append([5,5*(len(railway_lines)-1)]*int(len(xxx)/2-0.5)+[5])
            
    
    source = ColumnDataSource({'xs':xx,'ys':yy,'line_dash':dashes})
    
    if len(railway_lines) == 1:
        line_dash = 'solid'
    else:
        line_dash = 'line_dash'
             
    for cnt,railway_line in enumerate(railway_lines):

            railway_line = railway_line.strip()

            p.multi_line('xs',
                   'ys',
                   source=source,
                   line_width=2,
                   #legend_label=str(railway_line),
                   line_color = color_mapping[railway_line],
                   line_dash = line_dash,
                   line_dash_offset = cnt*5
                  )

    
    
# plot the stations and add a hover tool
map_df = df_station_subway[['id','lat','lon','key','tags','tag','name','line','colour','operator']].copy()

map_df["x"],map_df["y"] = TRANSFORM_4326_TO_3857.transform(map_df['lat'],map_df['lon'])  
map_df["coordinates"]=tuple(zip(map_df["lat"],map_df["lon"]))
map_df['tags'] = map_df['tags'].apply(str)
map_df['tag'] = map_df['tag'].apply(str)
map_df['key'] = map_df['key'].apply(str)
map_df['line'] = map_df['line'].fillna('Other')

stations = list()
for legend_group in set(map_df["line"]):
    
    source = ColumnDataSource(map_df.loc[map_df["line"]==legend_group])

    
    station_lines = legend_group.split(';')
        
    for cnt,station_line in enumerate(station_lines):
        
        if len(station_lines)>1:
            
            station = p.wedge(x="x", y="y",
                            source=source,
                            start_angle=(cnt-1)/len(station_lines)*2*3.142,
                            end_angle=cnt/len(station_lines)*2*3.1412,
                            radius=100,
                            line_width=1,
                            fill_color = color_mapping[station_line],
                            line_color = 'white',
                            legend_label=station_line
                            )
            
        else:
        
            station = p.circle(x="x", y="y",
                            source=source,
                            radius=100,
                            line_width=1,
                            fill_color = color_mapping[station_line],
                            line_color = 'white',
                            legend_label=station_line
                            )
            
        stations.append(station)
    

p.add_tools(HoverTool(tooltips=tooltips, renderers=stations))

p.legend.click_policy="hide"
    
    
show(p)

In [29]:
df_railways = pd.DataFrame()

df_metro = osm.toolkit.get_osm_data(key=tags.name__en,tag="Paris Metro",area="")

df_metro_lines = pd.DataFrame.from_records(df_metro['members'][0])

for metro_line_id in df_metro_lines['ref']:
    
    #print(metro_line_id)
    
    df_metro_line = osm.toolkit.get_osm_data_by_id(member_id=metro_line_id,obj_type="rel")
    
    #print(df_metro_line.iloc[0]['name'])
    
    df_metro_routes = pd.DataFrame.from_records(df_metro_line['members'][0])
    
    for route in df_metro_routes['ref']:
        
        df_metro_route = osm.toolkit.get_osm_data_by_id(member_id=route,obj_type="rel",output="geom")
    
        if not df_metro_route.empty:
            
            members = pd.DataFrame.from_records(df_metro_route.iloc[0]['members'])
            rails = members[members['role']==""]
            stations = members[members['role']=="station"]
            stops = members[members['role']=="stop"]

            if not rails.empty:            
                df_metro_route['rails'] = [rails['geometry']]

            if not stations.empty:
                df_metro_route['stations'] = [stations[['ref','lat','lon']]]

            if not stops.empty:
                stop_ids = str(list(stops['ref'])).replace('[','').replace(']','')
                stops_info = osm.toolkit.get_osm_data_by_id(member_id="id:"+stop_ids,obj_type="node")  
                df_metro_route['stops'] = [stops_info]

            df_railways = pd.concat([df_railways,df_metro_route])
        
        #print(df_railways)
    

No specified nodes found in area
No specified nodes found in area
No specified nodes found in area
No specified nodes found in area


In [30]:
from bokeh.plotting import figure
from bokeh.models import WMTSTileSource, ColumnDataSource
from bokeh.models import HoverTool

from pyproj import Transformer

# Use pyproj to transform longitude and latitude into web-mercator and add to a copy of the asset dataframe
TRANSFORM_4326_TO_3857 = Transformer.from_crs("EPSG:4326", "EPSG:3857")
    
# create a plot of the subway system    
output_file("Paris_subway.html")

p = figure(plot_width=800, plot_height=800,
                    x_axis_type="mercator", y_axis_type="mercator")

MAP_TILES = {"OpenMap": WMTSTileSource(url="http://c.tile.openstreetmap.org/{Z}/{X}/{Y}.png"),
         "ESRI": WMTSTileSource(url="https://server.arcgisonline.com/ArcGIS/rest/services/World_Imagery/MapServer/tile/{Z}/{Y}/{X}.jpg"),
         "OpenTopoMap": WMTSTileSource(url="https://tile.opentopomap.org/{Z}/{X}/{Y}.png")}
    
p.add_tile(MAP_TILES['ESRI'])

tooltips = [("id", "@id"),
            ("name", "@name"),
            ("line", "@line"),
            ("network", "@network"),
            ("operator", "@operator"),
            ("(lat,lon)", "@coordinates")]

stations = list()

# plot the railway lines    
for cnt,line in df_railways.iterrows():

    #print(line['name'])
    
    xx = list()
    yy = list()
    
    for way in line['rails'].dropna():
    

        xxx,yyy = TRANSFORM_4326_TO_3857.transform(list(pd.DataFrame.from_records(way)['lat']),
                                                 list(pd.DataFrame.from_records(way)['lon']))

        xx.append(xxx)
        yy.append(yyy)

        
    source = ColumnDataSource({'xs':xx,'ys':yy})
    
    p.multi_line('xs',
           'ys',
           source=source,
           line_width=2,
           legend_label=line['short_name'],
           line_color = line['colour'],
          )

    
    line['stops']['xs'],line['stops']['ys'] = TRANSFORM_4326_TO_3857.transform(list(line['stops']['lat']),
                                                 list(line['stops']['lon']))
    
    line['stops']['coordinates'] = tuple(zip(line['stops']["lat"],line['stops']["lon"]))
    
    line['stops']['line'] = line['short_name']
    line['stops']['network'] = line['network']
    line['stops']['operator'] = line['operator']
    
    source = ColumnDataSource(line['stops'])
    
    station = p.circle(x="xs", y="ys",
                            source=source,
                            radius=100,
                            line_width=1,
                            fill_color = line['colour'],
                            line_color = 'white',
                            legend_label=line['short_name']
                            )
    
    
    stations.append(station)
    

p.add_tools(HoverTool(tooltips=tooltips, renderers=stations))

p.legend.click_policy="hide"


show(p)    


In [36]:
df_railways = pd.DataFrame()

df_metro = osm.toolkit.get_osm_data_by_id(member_id=7225135,obj_type="rel") #London metro OSM ID 7225135

df_metro_lines = pd.DataFrame.from_records(df_metro['members'][0])

for metro_line_id in df_metro_lines['ref']:
    
    #print(metro_line_id)
    
    df_metro_line = osm.toolkit.get_osm_data_by_id(member_id=metro_line_id,obj_type="rel")
    
    #print(df_metro_line.iloc[0]['name'])
    
    df_metro_routes = pd.DataFrame.from_records(df_metro_line['members'][0])
    
    for route in df_metro_routes['ref']:
        
        df_metro_route = osm.toolkit.get_osm_data_by_id(member_id=route,obj_type="rel",output="geom")
    
        if not df_metro_route.empty:
            
            members = pd.DataFrame.from_records(df_metro_route.iloc[0]['members'])
            rails = members[members['role']==""]
            stations = members[members['role']=="station"]
            stops = members[(members['role']=="stop") | (members['role']=="stop_entry_only") | (members['role']=="stop_exit_only")]

            if not rails.empty:            
                df_metro_route['rails'] = [rails['geometry']]

            if not stations.empty:
                df_metro_route['stations'] = [stations[['ref','lat','lon']]]

            if not stops.empty:
                stop_ids = str(list(stops['ref'])).replace('[','').replace(']','')
                stops_info = osm.toolkit.get_osm_data_by_id(member_id="id:"+stop_ids,obj_type="node")  
                df_metro_route['stops'] = [stops_info]

            df_railways = pd.concat([df_railways,df_metro_route])
        
        #print(df_railways)
    

In [37]:
from bokeh.plotting import figure
from bokeh.models import WMTSTileSource, ColumnDataSource
from bokeh.models import HoverTool

from pyproj import Transformer

# Use pyproj to transform longitude and latitude into web-mercator and add to a copy of the asset dataframe
TRANSFORM_4326_TO_3857 = Transformer.from_crs("EPSG:4326", "EPSG:3857")
    
# create a plot of the subway system    
output_file("London_metro.html")

p = figure(plot_width=800, plot_height=800,
                    x_axis_type="mercator", y_axis_type="mercator")

MAP_TILES = {"OpenMap": WMTSTileSource(url="http://c.tile.openstreetmap.org/{Z}/{X}/{Y}.png"),
         "ESRI": WMTSTileSource(url="https://server.arcgisonline.com/ArcGIS/rest/services/World_Imagery/MapServer/tile/{Z}/{Y}/{X}.jpg"),
         "OpenTopoMap": WMTSTileSource(url="https://tile.opentopomap.org/{Z}/{X}/{Y}.png")}
    
p.add_tile(MAP_TILES['ESRI'])

tooltips = [("id", "@id"),
            ("name", "@name"),
            ("line", "@line"),
            ("network", "@network"),
            ("operator", "@operator"),
            ("(lat,lon)", "@coordinates")]

station_glpyhs = list()

# plot the railway lines    
for cnt,line in df_railways.iterrows():

    #print(line['name'])
    
    xx = list()
    yy = list()
    
    for way in line['rails'].dropna():
    

        xxx,yyy = TRANSFORM_4326_TO_3857.transform(list(pd.DataFrame.from_records(way)['lat']),
                                                 list(pd.DataFrame.from_records(way)['lon']))

        xx.append(xxx)
        yy.append(yyy)

        
    source = ColumnDataSource({'xs':xx,'ys':yy})
    
    p.multi_line('xs',
           'ys',
           source=source,
           line_width=2,
           legend_label=line['ref'],
           line_color = line['colour'],
          )

    if isinstance(line['stops'],pd.DataFrame):
    
        line['stops']['xs'],line['stops']['ys'] = TRANSFORM_4326_TO_3857.transform(list(line['stops']['lat']),
                                                     list(line['stops']['lon']))

        line['stops']['coordinates'] = tuple(zip(line['stops']["lat"],line['stops']["lon"]))

        line['stops']['line'] = line['ref']
        line['stops']['network'] = line['network']
        line['stops']['operator'] = line['operator']

        source = ColumnDataSource(line['stops'])

        station = p.circle(x="xs", y="ys",
                                source=source,
                                radius=100,
                                line_width=1,
                                fill_color = line['colour'],
                                line_color = 'white',
                                legend_label=line['ref']
                                )


        station_glpyhs.append(station)


p.add_tools(HoverTool(tooltips=tooltips, renderers=station_glpyhs))

p.legend.click_policy="hide"


show(p)    


In [38]:
df_railways = pd.DataFrame()

df_metro = osm.toolkit.get_osm_data_by_id(member_id=2621040,obj_type="rel")

df_metro_lines = pd.DataFrame.from_records(df_metro['members'][0])

for metro_line_id in df_metro_lines['ref']:
    
    #print(metro_line_id)
    
    df_metro_line = osm.toolkit.get_osm_data_by_id(member_id=metro_line_id,obj_type="rel")
    
    #print(df_metro_line.iloc[0]['name'])
    
    df_metro_routes = pd.DataFrame.from_records(df_metro_line['members'][0])
    
    for route in df_metro_routes['ref']:
        
        df_metro_route = osm.toolkit.get_osm_data_by_id(member_id=route,obj_type="rel",output="geom")
    
        if not df_metro_route.empty:
            
            members = pd.DataFrame.from_records(df_metro_route.iloc[0]['members'])
            rails = members[members['role']==""]
            stations = members[members['role']=="station"]
            stops = members[(members['role']=="stop") | (members['role']=="stop_entry_only") | (members['role']=="stop_exit_only")]

            if not rails.empty:            
                df_metro_route['rails'] = [rails['geometry']]

            if not stations.empty:
                df_metro_route['stations'] = [stations[['ref','lat','lon']]]

            if not stops.empty:
                stop_ids = str(list(stops['ref'])).replace('[','').replace(']','')
                stops_info = osm.toolkit.get_osm_data_by_id(member_id="id:"+stop_ids,obj_type="node")  
                df_metro_route['stops'] = [stops_info]

            df_railways = pd.concat([df_railways,df_metro_route])
        
        #print(df_railways)
    

In [39]:
from bokeh.plotting import figure
from bokeh.models import WMTSTileSource, ColumnDataSource
from bokeh.models import HoverTool

from pyproj import Transformer

# Use pyproj to transform longitude and latitude into web-mercator and add to a copy of the asset dataframe
TRANSFORM_4326_TO_3857 = Transformer.from_crs("EPSG:4326", "EPSG:3857")
    
# create a plot of the subway system    
output_file("NewYork_metro.html")

p = figure(plot_width=800, plot_height=800,
                    x_axis_type="mercator", y_axis_type="mercator")

MAP_TILES = {"OpenMap": WMTSTileSource(url="http://c.tile.openstreetmap.org/{Z}/{X}/{Y}.png"),
         "ESRI": WMTSTileSource(url="https://server.arcgisonline.com/ArcGIS/rest/services/World_Imagery/MapServer/tile/{Z}/{Y}/{X}.jpg"),
         "OpenTopoMap": WMTSTileSource(url="https://tile.opentopomap.org/{Z}/{X}/{Y}.png")}
    
p.add_tile(MAP_TILES['ESRI'])

tooltips = [("id", "@id"),
            ("name", "@name"),
            ("line", "@line"),
            ("network", "@network"),
            ("operator", "@operator"),
            ("(lat,lon)", "@coordinates")]

station_glpyhs = list()

# plot the railway lines    
for cnt,line in df_railways.iterrows():

    #print(line['name'])
    
    xx = list()
    yy = list()
    
    for way in line['rails'].dropna():
    

        xxx,yyy = TRANSFORM_4326_TO_3857.transform(list(pd.DataFrame.from_records(way)['lat']),
                                                 list(pd.DataFrame.from_records(way)['lon']))

        xx.append(xxx)
        yy.append(yyy)

        
    source = ColumnDataSource({'xs':xx,'ys':yy})
    
    p.multi_line('xs',
           'ys',
           source=source,
           line_width=2,
           legend_label=line['ref'],
           line_color = line['colour'],
          )

    if isinstance(line['stops'],pd.DataFrame):
    
        line['stops']['xs'],line['stops']['ys'] = TRANSFORM_4326_TO_3857.transform(list(line['stops']['lat']),
                                                     list(line['stops']['lon']))

        line['stops']['coordinates'] = tuple(zip(line['stops']["lat"],line['stops']["lon"]))

        line['stops']['line'] = line['ref']
        line['stops']['network'] = line['network']
        line['stops']['operator'] = line['operator']

        source = ColumnDataSource(line['stops'])

        station = p.circle(x="xs", y="ys",
                                source=source,
                                radius=100,
                                line_width=1,
                                fill_color = line['colour'],
                                line_color = 'white',
                                legend_label=line['ref']
                                )


        station_glpyhs.append(station)


p.add_tools(HoverTool(tooltips=tooltips, renderers=station_glpyhs))

p.legend.click_policy="hide"


show(p)    
